In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn

import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px

import plotly.io as pio
pio.templates.default = 'simple_white'
pio.orca.config.executable = '/Users/ngsk/opt/anaconda3/bin/orca'
#pio.orca.config.save()

from sklearn import linear_model
from scipy.optimize import curve_fit


In [2]:
export_path = '../contents/html/src/images/fig/'
export_html_path = '../contents/html/src/templates/fig/' 

export_path = 'docfig/'
export_html_path = 'docfig/' 

width = 950

def customLabels(fig, labels):
    for i, dat in enumerate(fig.data):
        for elem in dat:
            if elem == 'name':
                fig.data[i].name = labels[fig.data[i].name]
    return(fig)



In [3]:
# color system from SQUARE

colorset = dict(
    white='#fff',
    gray_100='#f9f9f9',
    gray_200='#eeeeee',
    gray_300='#dee2e6',
    gray_400='#c4c4c4',
    gray_500='#adb5bd',
    gray_600='#999999',
    gray_700='#495057',
    gray_800='#343a40',
    gray_900='#212529',
    black='#000',
    blue='#012545',
    indigo='#6610f2',
    purple='#6f42c1',
    pink='#e83e8c',
    red='#c7473f',
    orange='#fd7e14',
    yellow='#e1be5f',
    green='#60c39b',
    teal='#46c5af',
    cyan='#359bd0'
)

theme = dict(
    primary='#232323',
    secondary='#da3458',
    success=colorset['green'],
    info=colorset['cyan'],
    warning=colorset['yellow'],
    danger=colorset['red'],
    light=colorset['gray_400'],
    dark=colorset['gray_800'],
    gray=colorset['gray_600'],
    white=colorset['gray_100']
)


In [4]:
my_template = go.layout.Template()

my_template.layout = dict(
    title=dict(x=0.00,y=0.98,xanchor='left', yanchor='top'),
    font_family='Menlo',
    font_color=theme['light'],
    title_font = dict(size=10,color=theme['primary']),
    autosize=True,
    width=width,
    height=width/2,
    margin=dict(l=50, r=20, b=50, t=50, pad=0),
    showlegend=False)

my_template.data.scatter = [
    go.Scatter(line_color=theme['light']),
    go.Scatter(line_color=theme['info'])
    ]

my_template.layout.annotationdefaults = dict(
            font=dict(
                color=theme['primary'],
                size=9
            ),
            showarrow=True,
            arrowcolor=theme['primary'],
            arrowhead=1)

In [5]:

title = 'Average Temperature | SENDAI 1927-2019'
datasource = 'jma/average_monthly_temperature_SENDAI_1872-2020.csv'

df_sendai = pd.read_csv(datasource, header=3, index_col=0, usecols=[0,1])
df_sendai = df_sendai.dropna()

df_sendai.index = pd.to_datetime(df_sendai.index)
df_sendai.columns = ['SND']

# df_sendai = df_sendai.resample('Y').mean()
# df_sendai = df_sendai.loc['1927':]

df_sendai['SND_MA'] = df_sendai['SND'].rolling(window=12*3).mean()

#
X = df_sendai.index.year.values
y = df_sendai['SND'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_sendai['l_fit'] = a * X + b

(a,b), _ = curve_fit(lambda x,a,b: x ** a + b, X, y)
df_sendai['c_fit'] = X ** a + b

#
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_sendai.index, y=df_sendai['SND'], line_color=theme['light'], name='気温'
))
fig.add_trace(go.Scatter(
    x=df_sendai.index, y=df_sendai['l_fit'], line_color=theme['info'], name='トレンド'
))

title_font = dict(size=10, family='Menlo', color=theme['light'])

fig.update_xaxes(title_text='', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='Temperature (ºC)',title_font=title_font, showline=True, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)

# fig.add_annotation(text='trend = {0:.2f}ºC/100yrs'.format(a * 10),
#                   xref='paper', yref='paper',
#                   x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=20, b=50, t=50, pad=0))

fig.show()

#
fig.write_image(export_path + 'fig1-1.svg')
fig.write_image(export_path + 'fig1-1.png')

# config = dict(
#     include_plotlyjs='cdn'
# )
fig.write_html(export_html_path + 'fig1-1.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)

In [6]:
help(go.Figure.write_html)

Help on function write_html in module plotly.basedatatypes:

write_html(self, *args, **kwargs)
    Write a figure to an HTML file representation
    
    Parameters
    ----------
    file: str or writeable
        A string representing a local file path or a writeable object
        (e.g. an open file descriptor)
    config: dict or None (default None)
        Plotly.js figure config options
    auto_play: bool (default=True)
        Whether to automatically start the animation sequence on page load
        if the figure contains frames. Has no effect if the figure does not
        contain frames.
    include_plotlyjs: bool or string (default True)
        Specifies how the plotly.js library is included/loaded in the output
        div string.
    
        If True, a script tag containing the plotly.js source code (~3MB)
        is included in the output.  HTML files generated with this option are
        fully self-contained and can be used offline.
    
        If 'cdn', a script ta

In [7]:

title = 'Average Temperature | TOKYO 1876-2019'
datasource = 'jma/average_monthly_temperature_TOKYO_1872-2020.csv'

df_tokyo = pd.read_csv(datasource, header=4, index_col=0, usecols=[0,1])
df_tokyo= df_tokyo.dropna()

df_tokyo.index = pd.to_datetime(df_tokyo.index)
df_tokyo.columns = ['TYO']

# df_tokyo = df_tokyo.resample('Y').mean()
# df_tokyo = df_tokyo.loc['1876':]

df_tokyo['TYO_MA'] = df_tokyo['TYO'].rolling(window=12*3).mean()

#
X = df_tokyo.index.year.values
y = df_tokyo['TYO'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_tokyo['l_fit'] = a * X + b

(a,b), _ = curve_fit(lambda x,a,b: x ** a + b, X, y)
df_tokyo['c_fit'] = X ** a + b

#
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_tokyo.index, y=df_tokyo['TYO'], line_color=theme['light'], name='気温'
))
fig.add_trace(go.Scatter(
    x=df_tokyo.index, y=df_tokyo['l_fit'], line_color=theme['info'], name='トレンド'
))

# fig.add_annotation(text='trend = {0:.2f}ºC/100yrs'.format(a * 10),
#                   xref='paper', yref='paper',
#                   x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

title_font = dict(size=10, family='Menlo', color=theme['light'])

fig.update_xaxes(title_text='', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='Temperature (ºC)',title_font=title_font, showline=True, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=20, b=50, t=50, pad=0))

fig.show()

#
fig.write_image(export_path + 'fig1-2.svg')
fig.write_image(export_path + 'fig1-2.png')

fig.write_html(export_html_path + 'fig1-2.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


In [8]:
# 気象庁｜世界の月平均気温偏差
# http://www.data.jma.go.jp/cpdinfo/temp/nov_wld.html
title = 'Global Average Temperature Deviation'

datasource = 'jma/Global monthly mean temperature deviation_mon_wld.csv'
df = pd.read_csv(datasource, header=0, encoding='shiftjis')

df.columns = ['year',1,2,3,4,5,6,7,8,9,10,11,12]

df = pd.melt(df, id_vars=['year'], var_name='month', value_name='temperature')

df['year'] = df['year'].astype(str)
df['month'] = df['month'].astype(str)
df['date'] = df['year'].str.cat(df['month'], sep='-')
df['date'] = pd.to_datetime(df['date'])
df = df.set_index('date')
df = df.dropna()
df = df.sort_index()

# df = df.resample('Y').mean()


#
X = df.index.year
y = df['temperature'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df['l_fit'] = a * X + b

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df.index,
    y=df['temperature'],
    name='気温偏差'
))

fig.add_trace(go.Scatter(
    x=df.index,
    y=df['l_fit'],
    name='トレンド'
))

#ig.add_vrect(x0=pd.to_datetime('1995'), x1=pd.to_datetime('2020'), annotation=dict(text='increase', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='Temperature (ºC)',title_font=title_font, showline=True, linecolor=theme['light'], tickcolor=theme['light'], zeroline=False)

fig.add_annotation(text='trend = {0:.2f}ºC/100yr'.format(a * 100),
                  xref='paper', yref='paper',
                  x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=20, b=50, t=50, pad=0))
fig.show()

#
fig.write_image(export_path + 'fig2.svg')
fig.write_image(export_path + 'fig2.png')

fig.write_html(export_html_path + 'fig2.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


In [9]:
# Fig 2-2
#  Seasons in Japan

title = 'Seasonal Average Temperature Deviation in Japan'
datasource = 'jma/ssn_jpn.csv'
seasonal_df = pd.read_csv(datasource, header=0, encoding='shiftjis')
seasonal_df.columns = ['year','Winter(12-2)','Spring(3-5)','Summer(6-8)','Autumn(9-11)']
seasonal_df = seasonal_df.set_index('year')

for index, (title,df) in enumerate(seasonal_df.iteritems(), 1):
    
    X = df.index
    y = df.values
    (a,b), _ = curve_fit(lambda x,a,b: a*x+b, X, y)

    print(a*10)
    
    fig = go.Figure()

    fig.add_trace(go.Scatter(
        x=df.index,
        y=df.values,
        name='気温偏差'
    ))

    fig.add_trace(go.Scatter(
        x=df.index,
        y=a * df.index + b,
        name='トレンド'
    ))

# Temperature Deviation(ºC)
# Year

    fig.update_xaxes(title_text='', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
    fig.update_yaxes(title_text='',title_font=title_font, showline=True, linecolor=theme['light'], tickcolor=theme['light'], zeroline=False, range=[-2.5, 2.5])

    fig.add_annotation(text='trend = {0:.2f}ºC/100yr'.format(a * 100),
                  xref='paper', yref='paper',
                  x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

    fig.update_layout(
        template=my_template,
        width=200,
        height=200,
        title=title,
        margin=dict(l=30, r=10, b=30, t=30, pad=0))
    fig.show()

    #
    fig.write_image(export_path + 'fig2-{0}.svg'.format(index))
    fig.write_html(export_html_path + 'fig2-{0}.html'.format(index),
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


0.1192651971253944


0.14874050315932424


0.1137428899191506


0.12567618311122303


In [11]:
# https://www.giss.nasa.gov/research/briefs/hansen_15/
title = 'Global Temperature Relative to Peak Holocene Temperature'
datasource = 'NASA_GISS/global_temperature_relative_to_peak_holocene/global_temp_rel_to_holocene.csv'

df_global_temp_rel = pd.read_csv(datasource, header=None)
df_global_temp_rel.columns = ['year','temperature']

# 年のデータを100万年に加工する
df_global_temp_rel['year'] = df_global_temp_rel['year'] * -1000000.0

df_global_temp_rel = df_global_temp_rel.sort_values('year')

#
X = df_global_temp_rel['year'].values
y = df_global_temp_rel['temperature'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_global_temp_rel['l_fit'] = a * X + b

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_global_temp_rel['year'],
    y=df_global_temp_rel['temperature'],
    name='気温偏差'
))

fig.add_vrect(x0=-800000, x1=0, annotation=dict(text='Last 800,000 Years', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.add_trace(go.Scatter(
    x=df_global_temp_rel['year'],
    y=df_global_temp_rel['l_fit'],
    name='トレンド'
))


fig.add_hline(y=1.5, line_dash='dot', line_color=colorset['red'], line_width=1, annotation_text='1.5ºC', annotation_font_size=9,annotation_position='top', annotation_font_color=colorset['red'])

fig.update_xaxes(title_text='Time (Millions of Years Before Present)', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='Temperature (ºC)',title_font=title_font, showline=True, linecolor=theme['light'], tickcolor=theme['light'])

fig.add_annotation(text='trend = {0:.2f}/1Myr'.format(a * 1000000),
                  xref='paper', yref='paper',
                  x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=20, b=50, t=50, pad=0))
fig.show()

#
fig.write_image(export_path + 'fig3.svg')
fig.write_image(export_path + 'fig3.png')

fig.write_html(export_html_path + 'fig3.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)

In [12]:
title = '過去80万年の気温の変動'
datasource = 'NASA_GISS/global_temperature_relative_to_peak_holocene/Last800.csv'

df_global_temp_last800 = pd.read_csv(datasource, header=None)
df_global_temp_last800.columns = ['year', 'temperature']
df_global_temp_last800['year'] = df_global_temp_last800['year'] * -1000000.0
df_global_temp_last800['year'] = df_global_temp_last800['year'].astype(np.int)

title = 'Last 800 Thousand Years | Global Temperature Relative to Peak Holocene Temperature'

#
X = df_global_temp_last800['year'].values
y = df_global_temp_last800['temperature'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_global_temp_last800['l_fit'] = a * X + b

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_global_temp_last800['year'],
    y=df_global_temp_last800['temperature'],
    name='気温偏差'
))

fig.add_hline(y=1.5, line_dash='dot', line_color=colorset['red'], line_width=1, annotation_text='1.5ºC', annotation_font_size=9,annotation_position='top', annotation_font_color=colorset['red'])

# fig.add_vrect(x0=-700000, x1=-600000, annotation=dict(text='', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)
# fig.add_vrect(x0=-500000, x1=-400000, annotation=dict(text='', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)
# fig.add_vrect(x0=-300000, x1=-200000, annotation=dict(text='', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)
# fig.add_vrect(x0=-100000, x1=-000000, annotation=dict(text='', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.add_trace(go.Scatter(
    x=df_global_temp_last800['year'],
    y=df_global_temp_last800['l_fit'],
    name='トレンド'
))

fig.update_xaxes(title_text='Time (Thousand of Years Before Present)', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='Temperature (ºC)',title_font=title_font, showline=True, linecolor=theme['light'], tickcolor=theme['light'])

fig.add_annotation(text='trend = {0:.2f}/100kyr'.format(a * 100000),
                  xref='paper', yref='paper',
                  x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=20, b=50, t=50, pad=0))
fig.show()

#
fig.write_image(export_path + 'fig4.svg')
fig.write_image(export_path + 'fig4.png')

fig.write_html(export_html_path + 'fig4.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


In [13]:
# Milankovich Cycle
# http://www.climatedata.info/forcing/milankovitch-cycles/
title = '25万年前から現在までのミランコビッチサイクルと気温' 
title = 'Milankovich Cycles and Temperature from Vostok Ice-core' 
datasource = 'climatedata.info - Milankovich Cycle/NATURAL OR ANTHROPOGENIC CLIMATE CHANGE FORCING/Milankovitch/orbital time-tpt-inc.csv'

df_Milankovich = pd.read_csv(datasource, header=4, index_col=0)

fig = make_subplots(specs=[[{'secondary_y':True}]])
fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title)

fig.add_trace(go.Scatter(
    x=df_Milankovich.index,
    y=df_Milankovich['Temp'],
    name='気温偏差',
    line_color=theme['info'],
    line_shape='spline'), secondary_y=False)

fig.add_trace(go.Scatter(
    x=df_Milankovich.index,
    y=df_Milankovich['SI'],
    name='SI',
    line_color=colorset['pink'],
    line_shape='spline'), secondary_y=True)

# fig.add_vrect(x0=-240000, x1=-130000, annotation=dict(text='', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)


title_font = dict(size=10, family='Menlo')

fig.update_xaxes(title_text='Years relative to present', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)

fig.update_yaxes(title_text="Temperature (ºC)", secondary_y=False, title_font=title_font, 
title_font_color=theme['info'], linecolor=theme['light'], tickcolor=theme['light'], zeroline=False)

fig.update_yaxes(title_text="Solar Irradiance (W m−2)", secondary_y=True, title_font=title_font,title_font_color=colorset['pink'], linecolor=theme['light'], tickcolor=theme['light'], zeroline=False)

fig.show()

#
fig.write_image(export_path + 'fig5.svg')
fig.write_image(export_path + 'fig5.png')

fig.write_html(export_html_path + 'fig5.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)

In [14]:
# CO2
# https://www.co2levels.org/#sources
title = '過去80万年の二酸化炭素の変動'
datasource = 'co2levels.org#sources/800,000 YEARS AGO - 1000 YEARS AGO_ghg-concentrations_fig-1.txt'

df_co2_800t1t = pd.read_csv(datasource,header=6, usecols=[0,1])
df_co2_800t1t.columns = ['year','co2']
df_co2_800t1t = df_co2_800t1t.dropna()
df_co2_800t1t['year'] = df_co2_800t1t['year'].astype(np.int)

df_co2_800t1t = df_co2_800t1t[df_co2_800t1t['year'] < 0]

title = 'Last 800,000 Years | Global CO2'

#
X = df_co2_800t1t['year'].values
y = df_co2_800t1t['co2'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_co2_800t1t['l_fit'] = a * X + b

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_co2_800t1t['year'],
    y=df_co2_800t1t['co2'],
    fill='tozeroy',
    line_color=theme['light'],
    name='CO2'
))

fig.add_trace(go.Scatter(
    x=df_co2_800t1t['year'],
    y=df_co2_800t1t['l_fit'],
    name='トレンド'
))

fig.update_xaxes(title_text='Time (Thousand of Years Before Present)', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='CO2 (ppm)',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'], range=[0,450],zeroline=False)

fig.add_vrect(x0=-5000, x1=0, annotation=dict(text='Last 5,000 Years', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.add_annotation(text='trend = {0:.2f}/100kyr'.format(a * 100000),
                  xref='paper', yref='paper',
                  x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=20, b=50, t=50, pad=0))
fig.show()

#
fig.write_image(export_path + 'fig6.svg')
fig.write_image(export_path + 'fig6.png')

fig.write_html(export_html_path + 'fig6.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


In [15]:
# Temperature & CO2

title = '過去80万年の気温と二酸化炭素の変動'
df = pd.merge(df_co2_800t1t, df_global_temp_last800, on='year', how='outer')

title = 'Last 800,000 Years | Global Temperature and CO2'
#
fig = make_subplots(specs=[[{'secondary_y':True}]])


fig.add_trace(go.Scatter(
    x=df_co2_800t1t['year'], y=df['co2'], line_color=theme['light'],fill='tozeroy', name='CO2'), secondary_y=True)

fig.add_trace(go.Scatter(
    x=df['year'], y=df['temperature'],line_color=theme['info'], name='気温偏差'), secondary_y=False)

fig.add_vrect(x0=-5000, x1=0, annotation=dict(text='Last 5,000 Years', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)

title_font = dict(size=10, family='Menlo')

fig.update_xaxes(title_text='Time (Thousand of Years Before Present)', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'], zeroline=False)
fig.update_yaxes(title_text="Temperature (ºC)", secondary_y=False, range=[-6,2], title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'], zeroline=False, title_font_color=theme['info'])
fig.update_yaxes(title_text="CO2 (ppm)", secondary_y=True, range=[0,450], title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False, title_font_color=theme['light'])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=20, b=50, t=50, pad=0))
fig.show()

#
fig.write_image(export_path + 'fig7.svg')
fig.write_image(export_path + 'fig7.png')

fig.write_html(export_html_path + 'fig7.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)

last800_co2_mean = df['co2'].mean()


In [47]:
last800_co2_mean

229.8568901303538

In [16]:
# CO2 1000 YEARS AGO - 1975

title='1000 - 1975年の二酸化炭素量(ppm)'
datasource = 'co2levels.org#sources/1000 YEARS AGO - 1958 _lawdome.combined.dat'

df_co2_lawdome = pd.read_csv(datasource, sep='     ', header=251, index_col=0)
df_co2_lawdome = df_co2_lawdome.dropna(axis=1)
df_co2_lawdome.index.name = 'year'

#
fig = px.area(
    df_co2_lawdome, x=df_co2_lawdome.index, y='ppm',
    title=title,
    width=width,
    labels={})
fig.show()



In [17]:
# CO2 1958 - PRESENT

title = '1958年-現在までの二酸化炭素量(ppm)'
datasource = 'co2levels.org#sources/1958 - PRESENT DAY_co2_annmean_mlo.txt'

df_co2_1958toPRESENT = pd.read_csv(datasource, sep='  ', header=56, index_col=0)
df_co2_1958toPRESENT = df_co2_1958toPRESENT.dropna(axis=1)
df_co2_1958toPRESENT.columns = ['ppm','unc']
df_co2_1958toPRESENT = df_co2_1958toPRESENT.drop('unc', axis=1)
df_co2_1958toPRESENT.index.name = 'year'

#
fig = px.area(
    df_co2_1958toPRESENT, x=df_co2_1958toPRESENT.index, y='ppm',
    title=title,
    width=width,
    labels={})
fig.show()


In [18]:
# CO2 1000 Years Ago - Present

title='1000年-現在までの二酸化炭素量(ppm)'
df_co2_all = df_co2_lawdome.append(df_co2_1958toPRESENT.loc['1980'::])
# df_co2_all = df_co2_all.reset_index()
df_co2_all['year'] = df_co2_all.index
df_co2_all.columns = ['co2','year']

title = 'Global CO2 1000-2019'
#
X = df_co2_all['year'].values
y = df_co2_all['co2'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_co2_all['l_fit'] = a * X + b

# (a,b), _ = curve_fit(lambda x,a,b: a * np.exp(b*x), X, y, p0=(a,b))
# df_co2_all['c_fit'] = a * np.exp(b*X)

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_co2_all['year'],
    y=df_co2_all['co2'],
    fill='tozeroy',
    line_color=theme['light'],
    name='CO2'
))

fig.add_trace(go.Scatter(
    x=df_co2_all['year'],
    y=df_co2_all['l_fit'],
    name='トレンド'
))

fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='CO2 (ppm)',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'], range=[200,450],zeroline=False)

fig.add_vrect(x0=1840, x1=2019, annotation=dict(text='After The Industrial Revolution', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.add_hline(y=last800_co2_mean, line_dash='dot', line_color=colorset['red'], line_width=1, annotation_text='Average Global CO2 Levels (Last 800,000 Years)', annotation_font_size=9,annotation_position="bottom left", annotation_font_color=colorset['red'])

fig.add_annotation(text='trend = {0:.2f}/100yr'.format(a * 100),
                  xref='paper', yref='paper',
                  x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=50, b=50, t=50, pad=0))
fig.show()

#
fig.write_image(export_path + 'fig8.svg')

fig.write_html(export_html_path + 'fig8.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


In [20]:
df_AfterIR = df_co2_all.loc[1840:]

title = 'Global CO2 | After The Industorial Revolution 1840 - 2019'
#
X = df_AfterIR['year'].values
y = df_AfterIR['co2'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_AfterIR['l_fit'] = a * X + b

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df_AfterIR['year'],
    y=df_AfterIR['co2'],
    fill='tozeroy',
    line_color=theme['light'],
    name='CO2'
))

# fig.add_trace(go.Scatter(
#     x=df.index.year',
#     y=df['temperature'],
#     line_color=theme['info']
# ))

fig.add_trace(go.Scatter(
    x=df_AfterIR['year'],
    y=df_AfterIR['l_fit'],
    name='トレンド'
))

#
pre_IR_mean = df_AfterIR.loc['1850':'1900','co2'].mean()

# fig.add_hline(y=last800_co2_mean, line_dash='dot', line_color=colorset['red'], line_width=1, annotation_text='Average Global CO2 Levels (Last 800,000 Years)', annotation_font_size=9,annotation_position="bottom left", annotation_font_color=colorset['red'])

fig.add_hline(y=pre_IR_mean, line_dash='dot', line_color=colorset['red'], line_width=1, annotation_text='1850-1900 Average (290.06ppm)', annotation_font_size=9,annotation_position="top left", annotation_font_color=colorset['red'])


fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='CO2 (ppm)',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'], range=[200,450],zeroline=False)

fig.add_annotation(text='trend = {0:.2f}/100yr'.format(a*100),
                  xref='paper', yref='paper',
                  x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=50, b=50, t=50, pad=0))
fig.show()

#
fig.write_image(export_path + 'fig9.svg')
fig.write_image(export_path + 'fig9.png')

fig.write_html(export_html_path + 'fig9.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)

290.0636363636363

In [21]:

title = 'Global CO2 | After The Industorial Revolution 1840 - 2019'
df_AfterIR = df_co2_all.loc[1840:]

# 気象庁｜世界の月平均気温偏差
# http://www.data.jma.go.jp/cpdinfo/temp/nov_wld.html
title = 'Global Average Temperature Deviation and CO2 | 1890-2019'

datasource = 'jma/Global monthly mean temperature deviation_mon_wld.csv'
df = pd.read_csv(datasource, header=0, encoding='shiftjis')

df.columns = ['year',1,2,3,4,5,6,7,8,9,10,11,12]

df = pd.melt(df, id_vars=['year'], var_name='month', value_name='temperature')

df['year'] = df['year'].astype(str)
df['month'] = df['month'].astype(str)
df['date'] = df['year'].str.cat(df['month'], sep='-')
df['date'] = pd.to_datetime(df['date'])
df = df.set_index('date')
df = df.dropna()
df = df.sort_index()
df = df.resample('Y').mean()


#
fig = make_subplots(specs=[[{'secondary_y':True}]])


# fig.add_trace(go.Scatter(
#     x=df_co2_800t1t['year'], y=df['co2'], line_color=theme['light'],fill='tozeroy'), secondary_y=True)

fig.add_trace(go.Scatter(
    x=df_AfterIR.loc['1890':, 'year'],
    y=df_AfterIR.loc['1890':, 'co2'],
    fill='tozeroy',
    line_color=theme['light'],
    name='CO2'),
    secondary_y=False
)

fig.add_trace(go.Scatter(
    x=df.index.year[:2019], y=df.loc[:'2019','temperature'],line_color=theme['info'], name='気温偏差'), secondary_y=True)

# fig.add_vrect(x0=-5000, x1=0, annotation=dict(text='Last 5,000 Years', font_size=9), fillcolor=colorset['green'], opacity=0.25, line_width=0)

title_font = dict(size=10, family='Menlo')

fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'], zeroline=False)

fig.update_yaxes(title_text="Temperature (ºC)", secondary_y=True, title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'], zeroline=False, title_font_color=theme['info'])

fig.update_yaxes(title_text="CO2 (ppm)", secondary_y=False, title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False, title_font_color=theme['light'], range=[250,420])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title,
    margin=dict(l=50, r=20, b=50, t=50, pad=0))
fig.show()


fig.write_image(export_path + 'fig9-2.svg')
fig.write_image(export_path + 'fig9-2.png')


fig.write_html(export_html_path + 'fig9-2.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)

In [21]:
df.head()

temperature
date                   
1891-12-31    -0.639167
1892-12-31    -0.718333
1893-12-31    -0.758333
1894-12-31    -0.709167
1895-12-31    -0.680000

In [53]:
# cut
,
bins = [1830,1900,1970,2040]
cut = pd.qcut(df_AfterIR.index, 5, precision=0)

for index,(cut,df) in enumerate(df_AfterIR.groupby(cut), 1):

    title = 'Global CO2 | {0}-{1}'.format(int(cut.left), int(cut.right))
    #
    X = df['year'].values
    y = df['co2'].values
    (a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
    df['l_fit'] = a * X + b

    fig = go.Figure()

    fig.add_trace(go.Scatter(
        x=df['year'],
        y=df['co2'],
        fill='tozeroy',
        line_color=theme['light'],
        mode='lines'
    ))

    fig.add_trace(go.Scatter(
        x=df['year'],
        y=df['l_fit'],
        mode='lines'))

    fig.add_hline(y=last800_co2_mean, line_dash='dot', line_color=colorset['red'], line_width=1, annotation_text='Last 800,000yr Average', annotation_font_size=9,annotation_position="bottom left", annotation_font_color=colorset['red'])

    fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
    fig.update_yaxes(title_text='',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'], range=[0,450],zeroline=False, showticklabels=False)

    fig.add_annotation(text='trend = {0:.2f}/yr'.format(a),
                  xref='paper', yref='paper',
                  x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

    fig.update_layout(
        template=my_template,
        width=200,
        height=200,
        title=title,
        margin=dict(l=10, r=10, b=50, t=50, pad=0))
    fig.show()

    #
    fig.write_image(export_path + 'fig9-{0}.svg'.format(index))


In [22]:
# EM-DAT The international Disaster Database
datasource = 'public.emdat.be - Disaster/emdat_public_2020_11_15_query_uid-aBEhxs.xlsx'
df_dis = pd.read_excel(datasource, header=6)
df_dis['count'] = 1

In [25]:
# 災害件数の推移
title = '世界の災害件数の推移 1900-2020'

d = df_dis.groupby('Year').sum()
d['ma'] = d['count'].rolling(window=5).mean()

title = 'Annual Number of Global Disaster Events | 1900-2020'

fig = go.Figure()

fig.add_trace(go.Bar(x=d.index, y=d['count'], name='災害件数', marker_color=theme['info']))

# fig.add_trace(go.Scatter(x=d.index, y=d['ma'], name='移動平均(5年)',line_shape='spline', line_color=theme['info']))

fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='Disaster events',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False, range=[0,600])

fig.add_vrect(x0=2002, x1=2020, annotation=dict(text='decrease', font_size=9, font_color=colorset['green']), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title)
fig.show()

#
fig.write_image(export_path + 'fig10.svg')
fig.write_image(export_path + 'fig10.png')

fig.write_html(export_html_path + 'fig10.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


In [24]:
# 災害の種類内訳
title = '災害種類別の件数 1900-2020'

disaster_type_dict_ja = {'Animal accident':'動物の事故',
'Fog':'霧',
'Impact':'地球外衝撃',
'Mass movement (dry)':'落石等',
'Insect infestation':'虫害',
'Volcanic activity':'火山活動',
'Wildfire':'山火事',
'Extreme temperature':'極端な気温',
'Drought':'干ばつ',
'Landslide':'地滑り',
'Epidemic':'疫病',
'Earthquake':'地震',
'Storm':'嵐',
'Flood':'洪水'}

df_dis['ja'] = df_dis['Disaster Type'].apply(lambda d: disaster_type_dict_ja[d])

df = df_dis.groupby('ja')['count'].sum()

title = 'Global Disaster Events by Type | 1900-2020'
# plotly
fig = go.Figure()

df = df.sort_values(ascending=True)
fig.add_trace(go.Bar(
    x=df.values, y=df.index, name='Disaster', orientation='h', text=df.values, textposition='auto',marker_color=theme['info']))

fig.update_xaxes(title_text='Number of Events', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'],tickfont_color=theme['primary'],zeroline=False)

fig.update_layout(
    template=my_template,
    width=800,
    height=350,
    title=title,
    margin=dict(l=80))
fig.show()

#
fig.write_image(export_path + 'fig11.svg')

fig.write_html(export_html_path + 'fig11.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)



In [78]:
title = '災害種類別の件数推移 1900-2020'

datasource = 'public.emdat.be - Disaster/emdat_public_2020_11_15_query_uid-aBEhxs.xlsx'
df_dis = pd.read_excel(datasource, header=6)
df_dis['count'] = 1

df = df_dis[df_dis['Disaster Type'] == 'Extreme temperature']

d = df.groupby('Year')['count'].sum()

# df = df.sort_values(ascending=False)

# for key in df.index:
#     d = df_dis[df_dis['Disaster Type']==key].groupby('Year').sum()
#     fig.add_trace(go.Scatter(
#         x=d.index, y=d['count'], name=key, fill='tozeroy'))

# fig.show()

title = 'Extreme temperature | Annual Number of Global Disaster Events | 1900-2020'

fig = go.Figure()

fig.add_trace(go.Bar(x=d.index, y=d.values, marker_color=theme['info']))

# fig.add_trace(go.Scatter(x=d.index, y=d['ma'], name='移動平均(5年)',line_shape='spline', line_color=theme['info']))

fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='Disaster events',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False )

# fig.add_vrect(x0=2002, x1=2020, annotation=dict(text='decrease', font_size=9, font_color=colorset['green']), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title)
fig.show()

#
fig.write_image(export_path + 'fig11-2.svg')

fig.write_html(export_html_path + 'fig11-2.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


In [101]:
d.head()

Year
1936    2
1951    2
1953    3
1955    1
1958    2
Name: count, dtype: int64

In [91]:
df_dis['Disaster Type'].unique()

array(['Drought', 'Earthquake', 'Volcanic activity',
       'Mass movement (dry)', 'Storm', 'Flood', 'Epidemic', 'Landslide',
       'Wildfire', 'Extreme temperature', 'Fog', 'Insect infestation',
       'Impact', 'Animal accident'], dtype=object)

In [79]:
#
title = 'カテゴリ別災害件数 1900-2020'

df = df_dis.groupby('Disaster Subgroup')['count'].sum()
fig = go.Figure()
fig.update_layout(title=title, width=width)
df = df.sort_values(ascending=True)
fig.add_trace(
    go.Bar(x=df.values, y=df.index, orientation='h', text=df.values, textposition='auto'))
fig.show()

#
title = 'カテゴリ別災害件数の推移 1900-2020'
fig = go.Figure()
fig.update_layout(title=title, width=width)
df = df.sort_values(ascending=False)
for key in df.index:
    d = df_dis[df_dis['Disaster Subgroup']==key].groupby('Year').sum()
    fig.add_trace(
        go.Scatter(x=d.index, y=d['count'], name=key, fill='tozeroy'))

fig.show()



In [80]:
title = '災害による死者数と被害金額の推移'


title = 'Global Deaths from Disasters | 1900-2020'

dis_year_totaldeaths = df_dis.groupby('Year')['Total Deaths'].sum()
dis_year_totaldamage = df_dis.groupby('Year')['Total Damages (\'000 US$)'].sum()

df_totaldeaths_damages = pd.DataFrame({'deaths':dis_year_totaldeaths,'damage':dis_year_totaldamage})

df_totaldeaths_damages['ma_deaths'] = df_totaldeaths_damages['deaths'].rolling(window=5).mean()
df_totaldeaths_damages['ma_damage'] = df_totaldeaths_damages['damage'].rolling(window=5).mean()

# --- DEATHS
#
X = df_totaldeaths_damages.index.values
y = df_totaldeaths_damages['deaths'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_totaldeaths_damages['l_fit'] = a * X + b

fig = go.Figure()

fig.add_trace(
    go.Bar(x=df_totaldeaths_damages.index,y=df_totaldeaths_damages['deaths'], name='死者数', marker_color=theme['info']))

# fig.add_trace(go.Scatter(
#     x=df_totaldeaths_damages.index,
#     y=df_totaldeaths_damages['ma_deaths'],
#     line_color=theme['info'],
#     line_shape='spline'
# ))

fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='Deaths',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False, range=[0, 4500000])

fig.add_vrect(x0=1959, x1=2020, annotation=dict(text='decrease', font_size=9,font_color=colorset['green']), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title)
fig.show()

#
fig.write_image(export_path + 'fig12.svg')

fig.write_html(export_html_path + 'fig12.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


# ----- DAMAGES

title = 'Amount of Damage(US$) from Disasters | 1900-2020'
#
X = df_totaldeaths_damages.index.values
y = df_totaldeaths_damages['damage'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_totaldeaths_damages['l_fit'] = a * X + b

fig = go.Figure()

fig.add_trace(
    go.Bar(x=df_totaldeaths_damages.index,y=df_totaldeaths_damages['damage'], marker_color=colorset['pink']))

# fig.add_trace(go.Scatter(
#     x=df_totaldeaths_damages.index,
#     y=df_totaldeaths_damages['ma_damage'],
#     line_color=theme['info'],
#     line_shape='spline'
# ))

fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='Damages (US$)',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False, range=[0, 400000000])

fig.add_vrect(x0=1980, x1=2020, annotation=dict(text='increase', font_size=9,font_color=colorset['green']), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title)
fig.show()

#
fig.write_image(export_path + 'fig13.svg')

fig.write_html(export_html_path + 'fig13.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)


In [25]:
# CO2排出量
# 環境省
# https://www.env.go.jp/seisaku/list/ondanka.html


In [27]:
# 日本の温室効果ガス排出量 速報値 2020-12-08
# 国立環境研究所
# http://www.nies.go.jp/gio/aboutghg/index.html

title = '日本の温室効果ガス排出量の推移（2019年速報値）'
title = 'Greenhouse Gas Emissions in Japan | 2019'

datasource = 'nies.go.jp - CO2/L5-7gas_preliminary_2021-gioweb_1.0.xlsx'
df = pd.read_excel(datasource, sheet_name='1.Total')

# トリミング
df = df.iloc[:, 22:]
df.columns = np.arange(1,36)

#
co2_index = df.iloc[2:3, 4:33].values
co2_index = np.append(co2_index, 2019)
#
co2 = df.iloc[3:4, 4:34].values[0]
#
df_co2 = pd.DataFrame({'co2':co2}, index=pd.Index(co2_index, dtype=np.int))

# plotly
# fig = px.line(df_co2, x=df_co2.index, y='co2', line_shape='spline')
# fig.update_layout(title=title, width=width)
# fig.update_xaxes(title_text="（年度）")
# fig.update_yaxes(title_text="（単位　百万トンCO2 換算）")

# fig.show()

df_co2['co2'] = df_co2['co2'] * 1000000

#
X = df_co2.index.values
y = df_co2['co2'].values
(a,b), _ = curve_fit(lambda x,a,b: a * x + b, X, y)
df_co2['l_fit'] = a * X + b

fig = go.Figure()

fig.add_trace(
    go.Scatter(x=df_co2.index,y=df_co2['co2'], marker_color=theme['light'],line_shape='spline',fill='tozeroy',name='日本のCO2排出量'))

fig.add_trace(go.Scatter(
    x=df_co2.index,
    y=df_co2['l_fit'],
    line_color=theme['info'],
    name='トレンド'
))

fig.add_hline(y=df_co2.loc[1990]['co2'], line_dash='dot', line_color=colorset['red'], line_width=1, annotation_text='baseline', annotation_font_size=9,annotation_position="bottom left", annotation_font_color=colorset['red'])

fig.update_xaxes(title_text='Year', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False, range=[1990,2019])
fig.update_yaxes(title_text='CO₂',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False, range=[1000000000,1400000000])

# fig.add_vrect(x0=1980, x1=2020, annotation=dict(text='increase', font_size=9,font_color=colorset['green']), fillcolor=colorset['green'], opacity=0.25, line_width=0)

fig.add_annotation(text='trend = {0:.2f}/yr'.format(a / 1000000),
                  xref='paper', yref='paper',
                  x=0.0, y=1.0, showarrow=False, font_color=theme['info'])

fig.update_layout(
    template=my_template,
    width=800,
    height=300,
    title=title)
fig.show()

#
fig.write_image(export_path + 'fig14.svg')
fig.write_image(export_path + 'fig14.png')

fig.write_html(export_html_path + 'fig14.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)








In [124]:
df_co2.loc[1990]['co2']

1163873618.4377096

In [28]:
datasource = 'nies.go.jp - CO2/UNFCCC-GHG_J_200707.xlsx'
df = pd.read_excel(datasource, sheet_name='GHG total without LULUCF')
df.columns = np.arange(0, 33)
df = df.drop(index=[0,1,3,49,50,51,52,53,54], columns=[32])

#
df_GHG = df.loc[4:, 0:].copy()
df_GHG.columns = np.append(['country','country_en','baseline'],np.arange(1990,2019))

#
df_GHG = df_GHG.sort_values(ascending=False, by=df_GHG.columns[len(df_GHG.columns)-1])

#
import pycountry
def make_code(country_name):
    try:
        pc = pycountry.countries.search_fuzzy(country_name)[0]
        return pc.alpha_3
    except:
        return 'EU'
df_GHG['alpha_3'] = df_GHG['country_en'].apply(make_code)

#
df = pd.melt(df_GHG, id_vars=['country','country_en','baseline','alpha_3'], var_name='year', value_name='co2')
# df['co2'] = df['co2'].astype(np.float)
df['co2'] = df['co2'] * 1000

#
title = 'Greenhouse Gas Emissions (CO₂) by Country (excluding LULUCF) | 1990-2019'

rows = 9
cols = 5
grid = np.arange(1,rows*cols+1).reshape(rows,cols)
subplots_index = lambda x: (np.where(grid == x)[0][0]+1,np.where(grid == x)[1][0]+1)

fig = make_subplots(rows=rows, cols=cols, subplot_titles=df_GHG['country'].values,
    shared_xaxes=True,
    shared_yaxes=True,
    vertical_spacing=0.08,
    horizontal_spacing=0.08)

index = 1
for i,row in df_GHG.iterrows():
    fig.add_trace(go.Scatter(
        name=row.country,
        x=df_GHG.columns,
        y=row * 1000,
        fill='tozeroy',
        line_shape='linear',
        line_color=theme['info']),
        row=subplots_index(index)[0],
        col=subplots_index(index)[1])

    fig.add_hline(y=row.baseline*1000, line_dash='dot', line_width=1, line_color='red',
        row=subplots_index(index)[0],
        col=subplots_index(index)[1],
        annotation_text='')
    index = index + 1

fig.update_xaxes(matches='x')

for i in fig['layout']['annotations']:
    i['font']['size'] = 10

fig.update_xaxes(title_text='', title_font=title_font, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)
fig.update_yaxes(title_text='',title_font=title_font, title_font_color=theme['light'], showline=True, linecolor=theme['light'], tickcolor=theme['light'],zeroline=False)

fig.update_layout(
    template=my_template,
    width=800,
    height=1600,
    title=dict(text=title, y=0.996),
    margin=dict(t=80))
fig.show()

#
fig.write_image(export_path + 'fig15.svg')
fig.write_image(export_path + 'fig15.png')

fig.write_html(export_html_path + 'fig15.html',
    include_plotlyjs=False,
    include_mathjax=False,
    full_html=False)

In [83]:

title = '国別・温室効果ガス（LULUCFを除く）, kt（CO2換算）'
title = 'Greenhouse Gas Emissions by Country (excluding LULUCF)'

rows = 9
cols = 5
grid = np.arange(1,rows*cols+1).reshape(rows,cols)
subplots_index = lambda x: (np.where(grid == x)[0][0]+1,np.where(grid == x)[1][0]+1)

fig = make_subplots(rows=rows, cols=cols, subplot_titles=df_GHG['country'].values,
    shared_xaxes=True,
    shared_yaxes=True,
    vertical_spacing=0.08,
    horizontal_spacing=0.08)

index = 1
for i,row in df_GHG.iterrows():
    fig.add_trace(go.Scatter(
        name=row.country,
        x=df_GHG.columns,
        y=row * 1000,
        fill='tozeroy',
        line_shape='linear'),
        row=subplots_index(index)[0],
        col=subplots_index(index)[1])

    fig.add_hline(y=row.baseline*1000, line_dash='dot', line_width=1, line_color='red',
        row=subplots_index(index)[0],
        col=subplots_index(index)[1],
        annotation_text='')
    index = index + 1

fig.update_layout(title=title, width=950, height=1600, showlegend=False)
fig.update_xaxes(tickfont=dict(size=9), showline=False)
fig.update_yaxes(tickfont=dict(size=9))
fig.update_xaxes(matches='x')
for i in fig['layout']['annotations']:
    i['font']['size'] = 10
fig.show()


# これからのこと

In [27]:
title='部門別CO2排出量のシェア（電気・熱配分後）'

datasource = 'nies.go.jp - CO2/L5-7gas_preliminary_2021-gioweb_1.0.xlsx'
df = pd.read_excel(datasource, sheet_name='4.CO2-Share')
df.columns = np.arange(0,9)
df = df.drop(index=np.arange(0,15), columns=np.arange(0,2))

#
dep = df.loc[17:24, 2:2][2]
dep.name = 'department'

s1 = df.loc[17:24, 4:4][4]
s1.name = 2005

s2 = df.loc[17:24, 6:6][6]
s2.name = 2013

s3 = df.loc[17:24, 8:8][8]
s3.name = 2019

df_share = pd.concat([dep,s1,s2,s3], axis=1)

df_share.index = df_share['department']
df_share = df_share.drop(columns='department')

# plotly
specs = [[{'type':'domain'}, {'type':'domain'}, {'type':'domain'}]]
titles = [2005,2013,2019]
fig = make_subplots(rows=1, cols=3, specs=specs, subplot_titles=titles)

for i in [0,1,2]:
    fig.add_trace(go.Pie(
        direction='clockwise',
        labels=df_share.index,
        values=df_share[titles[i]],
        name=titles[i],
        scalegroup='one',
        hole=0.3), 1,i+1)

fig.update_layout(title=title, width=width)
fig.show()

#
df_share = df_share.reset_index()
df_share.columns = ['department','2005p','2013p','2019p']

#
df_share['2005'] = df_share['2005p'] * df_co2.loc[2005]['co2']
df_share['2013'] = df_share['2013p'] * df_co2.loc[2013]['co2']
df_share['2019'] = df_share['2019p'] * df_co2.loc[2019]['co2']

#
df_share = df_share.sort_values(ascending=False, by='2019')
df = pd.melt(df_share[['department','2005','2013','2019']], id_vars=['department'], var_name='year', value_name='co2')
fig = px.bar(df, x='year', y='co2', color='department')
fig.update_xaxes(type='category')
fig.update_layout(title=title, width=width)
fig.show()


In [31]:
# https://www.enecho.meti.go.jp/about/whitepaper/2019html/2-2-2.html
